In [ ]:
!pip uninstall -y torch torchvision torchaudio transformers accelerate bitsandbytes

!pip install -q torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

!pip install -q --upgrade transformers datasets accelerate evaluate scikit-learn pandas openpyxl geopy sentence-transformers peft ftfy seaborn matplotlib bitsandbytes country_converter pycountry



In [ ]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import torch
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
import re
import time
from datasets import Dataset, DatasetDict
from transformers import (
    AutoTokenizer,
    AutoModelForTokenClassification,
    AutoModelForSequenceClassification,
    pipeline,
    TrainingArguments,
    Trainer
)
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline, BitsAndBytesConfig
from tqdm.auto import tqdm
from geopy.geocoders import Nominatim
from geopy.distance import geodesic
from geopy.exc import GeocoderTimedOut, GeocoderUnavailable, GeocoderServiceError
from sentence_transformers import SentenceTransformer, util
import ftfy
from peft import LoraConfig, get_peft_model, TaskType
import evaluate
import difflib
from getpass import getpass
from google.colab import userdata
import huggingface_hub


In [ ]:
from huggingface_hub import login

hf_token = userdata.get('HF_TOKEN').strip()
huggingface_hub.login(token=hf_token)


Successfully logged into Hugging Face.


In [ ]:
tqdm.pandas()

geolocator = Nominatim(user_agent="news_location_llm_local_v1")
# embedding_model = SentenceTransformer('all-MiniLM-L6-v2')
embedding_model = SentenceTransformer('all-MiniLM-L6-v2', device='cuda')
location_cache = {}


In [ ]:
def sanitize_location_string(location_str: str):

    if not isinstance(location_str, str): return ""
    sanitized = re.sub(r'[^a-zA-Z\s,.-]', '', location_str)
    return re.sub(r'\s+', ' ', sanitized).strip()

In [ ]:
def clean_text(text: str):

    try:
        text = ftfy.fix_text(text)
        text = re.sub(r'http\S+|www\S+|https\S+', '', text, flags=re.MULTILINE)
        text = re.sub(r'\S*@\S*\s?', '', text, flags=re.MULTILINE)
        text = re.sub(r'\s+', ' ', text).strip()
    except Exception:
        return ""
    return text

In [ ]:
def get_first_n_sentences(text: str, n: int = 5):

    sentences = re.split(r'(?<=[.!?])\s+', text)
    return " ".join(sentences[:n])

In [ ]:
def is_valid_location(location):

    if not location:
        return False


    cleaned = location.replace("-", "").replace("‑", "").replace(".", "").strip()


    return len(cleaned) >= 2 and any(c.isalpha() for c in cleaned)

In [ ]:
ner_pipeline = pipeline("ner", model="dslim/bert-base-NER", device=0,aggregation_strategy="max")

Some weights of the model checkpoint at dslim/bert-base-NER were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Device set to use cuda:0


In [ ]:
def extract_locations(text: str):

    try:

        ner_results = ner_pipeline(text)
        locations = []

        for entity in ner_results:
            if entity['entity_group'] == 'LOC':
                location = entity['word'].strip()
                if is_valid_location(location):
                    locations.append(location)

        return list(set(locations))

    except Exception as e:
        print(f"NER extraction failed. Error: {e}")

        return extract_locations(text)

In [ ]:
def find_containing_sentence(text: str, phrase: str):

    escaped_phrase = re.escape(phrase)
    pattern = r'\b' + escaped_phrase + r'\b'
    for sentence in re.split(r'(?<=[.!?])\s+', text):
        if re.search(pattern, sentence, re.IGNORECASE):
            return sentence
    return get_first_n_sentences(text, 1)


In [ ]:
def geocode_with_retry(geolocator, query, limit=1, exactly_one=False):
    cache_key = f"{query}_{limit}_{exactly_one}"
    if cache_key in location_cache:
        return location_cache[cache_key]

    for attempt in range(3):
        try:
            time.sleep(1)
            locations = geolocator.geocode(query, language='en', limit=limit, exactly_one=exactly_one)
            location_cache[cache_key] = locations
            return locations
        except (GeocoderTimedOut, GeocoderUnavailable, GeocoderServiceError) as e:

            time.sleep(5 * (attempt + 1))
    location_cache[cache_key] = None
    return None

In [ ]:
def resolve_toponym(geolocator,text: str, candidate_str: str):

    if candidate_str is None:
        return None

    containing_sentence = find_containing_sentence(text, candidate_str)
    if not containing_sentence:

        return None


    gazetteer_entries = geocode_with_retry(geolocator, candidate_str, limit=5)
    if not gazetteer_entries or not isinstance(gazetteer_entries, list):
        return None

    try:
        sentence_embedding = embedding_model.encode(containing_sentence, convert_to_tensor=True)
        entry_names = [sanitize_location_string(entry.address) for entry in gazetteer_entries]
        entry_embeddings = embedding_model.encode(entry_names, convert_to_tensor=True)
        semantic_scores = util.cos_sim(sentence_embedding, entry_embeddings)[0].tolist()

        best_candidate = None
        highest_final_score = -1

        W_SEMANTIC = 0.4
        W_GAZETTEER = 0.4
        W_STRING = 0.2

        for i, entry in enumerate(gazetteer_entries):
            gazetteer_score = 1.0 - (i * 0.1)

            string_sim_score = difflib.SequenceMatcher(None, candidate_str.lower(), entry.address.split(',')[0].lower()).ratio()

            final_score = (
                (semantic_scores[i] * W_SEMANTIC) +
                (gazetteer_score * W_GAZETTEER) +
                (string_sim_score * W_STRING)
            )

            if final_score > highest_final_score:
                highest_final_score = final_score
                best_candidate = entry

        return best_candidate

    except Exception as e:
        print(f"Error during resolution for '{candidate_str}': {e}")
        return None

In [ ]:
def load_llama_pipeline():

    model_id = "meta-llama/Meta-Llama-3-8B-Instruct"

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
    )

    model = AutoModelForCausalLM.from_pretrained(
        model_id,
        quantization_config=bnb_config,
        device_map="cuda",
    )
    tokenizer = AutoTokenizer.from_pretrained(model_id)

    llama_pipeline = pipeline(
        "text-generation",
        model=model,
        tokenizer=tokenizer,
        torch_dtype=torch.float16,
        device_map="cuda",
    )
    return llama_pipeline

In [ ]:
def create_llama_prompt(article_text: str, candidates: list):

    system_prompt = "You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the list."
    candidate_list_str = "\n- ".join(candidates)
    user_prompt = f"""
Article:
"{article_text}"

Location Candidates:
- {candidate_list_str}

Based on the article, which of these candidates is the primary location of the main event?
Primary Location:"""

    messages = [
        {"role": "system", "content": system_prompt},
        {"role": "user", "content": user_prompt},
    ]
    return messages

In [ ]:
def get_llama_prediction(llama_pipeline, article_text: str, candidates: list):
    if not candidates:
        return "NO_CANDIDATES_RESOLVED"

    prompt_messages = create_llama_prompt(article_text, candidates)
    prompt = llama_pipeline.tokenizer.apply_chat_template(
        prompt_messages,
        tokenize=False,
        add_generation_prompt=True
    )

    terminators = [
        llama_pipeline.tokenizer.eos_token_id,
        llama_pipeline.tokenizer.convert_tokens_to_ids("<|eot_id|>")
    ]

    try:
        sequences = llama_pipeline(
            prompt,
            num_return_sequences=1,
            eos_token_id=terminators,
            max_new_tokens=50,
            do_sample=False,
            # temperature=0.6,
            # top_p=0.9,
        )
        prediction = sequences[0]['generated_text'][len(prompt):].strip()
        return prediction.split('\n')[0].strip()
    except Exception as e:
        print(f"An error occurred during Llama 3 inference: {e}")
        return "NO_PREDICTION_INFERENCE_ERROR"

In [ ]:
def check_overlap(string1, list2):
    words = string1.split()

    for word in words:
        for item in list2:
            if word.lower() in item.lower() or item.lower() in word.lower():
                return True
    return False

# **TEST DF**

In [ ]:
test_df = pd.read_excel("historic_data_of_risk_alerts_cleaned.xlsx")

In [ ]:
##### ALREADY CLEANED WITH ALL PRE-PROCESSING STEPS

test_df = pd.read_excel("historic_data_of_risk_alerts_cleaned.xlsx")

In [ ]:
test_df.head()
test_df.shape

(614, 2)

In [ ]:
test_df = test_df[["country","title","where","assessment"]].copy()
test_df.head()

KeyError: "None of [Index(['country', 'title', 'where', 'assessment'], dtype='object')] are in the [columns]"

In [ ]:
test_df = test_df.dropna(subset=['where'])

In [ ]:
test_df['assessment'] = test_df['assessment'].str.replace('<[^>]+>', '', regex=True)
test_df['Article'] = test_df['title'].fillna('').astype(str) + '. ' + test_df['assessment'].fillna('').astype(str)
test_df['Article']= test_df['Article'].apply(clean_text)
test_df.head()

country                                              title  \
0  Pakistan  Targeted Killing of CIA Officer in Muridke Rai...   
1  Pakistan  Public Holiday Declared on February 5 for Kash...   
2  Pakistan  Quetta-Punjab &Khyber Pakhtunkhwa Coach Servic...   
3  Pakistan  Deadly Dumper Accidents Claim Five Lives in Ka...   
4  Pakistan  Fatal Collision on Quetta-Karachi Highway Near...   

                                where  \
0                     Muridke, Punjab   
1                            Pakistan   
2  Quetta-Punjab & Khyber Pakhtunkhwa   
3                             Karachi   
4                     Quetta- Karachi   

                                          assessment  \
0  A Crime Investigation Agency (CIA) officer, Su...   
1  The federal government has declared Wednesday,...   
2  Passenger coach services from Quetta to Punjab...   
3  Karachi witnessed a spike in fatal accidents i...   
4  A high-speed collision involving three cars on...   

                                             Article  
0  Targeted Killing of CIA Officer in Muridke Rai...  
1  Public Holiday Declared on February 5 for Kash...  
2  Quetta-Punjab &Khyber Pakhtunkhwa Coach Servic...  
3  Deadly Dumper Accidents Claim Five Lives in Ka...  
4  Fatal Collision on Quetta-Karachi Highway Near...

In [ ]:
import re
def check_location_in_assessment(row):

    where_str = str(row['where']) if pd.notna(row['where']) else ''
    article_str = str(row['Article'])

    if not where_str or not article_str:
        return False

    where_words = {word for word in re.split(r'[,\s]+', where_str.lower()) if word}

    if not where_words:
        return True

    for word in where_words:
        if not re.search(r'\b' + re.escape(word) + r'\b', article_str, re.IGNORECASE):
            return False

    return True


rows_to_keep = test_df.apply(check_location_in_assessment, axis=1)

test_df = test_df[rows_to_keep]



print(f"\nNew number of rows: {len(test_df)}")

In [ ]:
def combine_location(row):
    where_str = str(row['where']) if pd.notna(row['where']) else ''
    country_str = str(row['country']) if pd.notna(row['country']) else ''

    if country_str.lower() in where_str.lower():
        return where_str
    else:

        return f"{where_str}, {country_str}".strip(', ')


test_df['Primary Location'] = test_df.apply(combine_location, axis=1)
test_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 821 entries, 1 to 1614
Data columns (total 6 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   country           821 non-null    object
 1   title             821 non-null    object
 2   where             821 non-null    object
 3   assessment        821 non-null    object
 4   Article           821 non-null    object
 5   Primary Location  821 non-null    object
dtypes: object(6)
memory usage: 44.9+ KB


In [ ]:
def is_location_resolvable(row):

  location_str = row['Primary Location']
  resolved_location = geocode_with_retry(geolocator, location_str, limit=1, exactly_one=True)

  if resolved_location:
    return True
  else:
    return False

print(f"Number of articles before filtering for resolvable locations: {len(test_df)}")

rows_to_keep = test_df.apply(is_location_resolvable, axis=1)

test_df = test_df[rows_to_keep]

print(f"Number of articles after filtering for resolvable locations: {len(test_df)}")


Number of articles before filtering for resolvable locations: 821


Number of articles after filtering for resolvable locations: 614


In [ ]:
test_df.to_excel('historic_data_of_risk_alerts_cleaned.xlsx', index=False)

In [ ]:
test_df = test_df[['Article','Primary Location']].copy()
test_df["Article"] = test_df["Article"].apply(get_first_n_sentences)
print(test_df.info())

test_df.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 614 entries, 0 to 613
Data columns (total 2 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Article           614 non-null    object
 1   Primary Location  614 non-null    object
dtypes: object(2)
memory usage: 9.7+ KB
None


Article  \
0  Public Holiday Declared on February 5 for Kash...   
1  Deadly Dumper Accidents Claim Five Lives in Ka...   
2  Fatal Collision on Quetta-Karachi Highway Near...   
3  BLF Claims Responsibility for Sniper Attack in...   
4  Gunmen Attack Construction Site in Khuzdar, Ba...   

                 Primary Location  
0                        Pakistan  
1               Karachi, Pakistan  
2       Quetta- Karachi, Pakistan  
3     Kech, Balochistan, Pakistan  
4  Khuzdar, Balochistan, Pakistan

# **Analysis**

In [ ]:
def run_analysis(llama_pipeline, dataset_path, output_filename):



  detailed_log_data = []

  detailed_log_data = []
  for _, row in tqdm(test_df.iterrows(), total=len(test_df), desc=f"Processing {dataset_path}"):
      article_text = row['Article']
      true_location_str = sanitize_location_string(row['Primary Location'])

      ner_candidates = extract_locations(article_text)

      if not ner_candidates:
        continue

      resolved_candidates = []
      for cand_str in ner_candidates:
          resolved = resolve_toponym(geolocator ,article_text, cand_str)
          if resolved:
              resolved_candidates.append(sanitize_location_string(resolved.address))
          else:
              resolved_candidates.append(sanitize_location_string(cand_str))

      if not resolved_candidates:
        continue

      pred_location_str = get_llama_prediction(llama_pipeline, article_text, list(set(resolved_candidates)))

      is_correct = False
      correctness_method = "Incorrect"
      resolved_true_str = ""
      resolved_pred_str = ""


      if "NO_" not in pred_location_str and true_location_str:
          true_loc_obj = resolve_toponym(geolocator, article_text, true_location_str)
          pred_loc_obj = resolve_toponym(geolocator, article_text, pred_location_str)

          if true_loc_obj and pred_loc_obj:
              true_loc_str = sanitize_location_string(true_loc_obj.raw.get('display_name'))
              pred_loc_str = sanitize_location_string(pred_loc_obj.raw.get('display_name'))

              distance = geodesic((true_loc_obj.latitude, true_loc_obj.longitude), (pred_loc_obj.latitude, pred_loc_obj.longitude)).kilometers
              if distance <= 50:
                  is_correct = True
                  correctness_method = "Distance"


              else:
                  true_location_list = true_loc_str.split(',')
                  pred_location_list = pred_loc_str.split(',')

                  if check_overlap(true_location_list[0], pred_location_list):
                    is_correct = True
                    correctness_method= "overlap resolved"

                  else:

                    true_location_list = true_location_str.split(',')
                    pred_location_list = pred_location_str.split(',')
                    if check_overlap(true_location_list[0], pred_location_list):
                        is_correct = True
                        correctness_method= "overlap resolved 2"

          else:
              true_location_list = true_location_str.split(',')
              pred_location_list = pred_location_str.split(',')
              if check_overlap(true_location_list[0], pred_location_list):
                  is_correct = True
                  correctness_method= "overlap not resolved"


      detailed_log_data.append({
            'Article': article_text,
            'NER_Candidates': ", ".join(ner_candidates),
            'Resolved_Candidates': ", ".join(resolved_candidates),
            'True_Location': row['Primary Location'],
            'Resolved_True_Location': true_loc_str,
            'Predicted_Location': pred_location_str,
            'Resolved_Predicted_Location': pred_loc_str,
            'Is_Correct': is_correct,
            'Correctness_Method': correctness_method
        })


  log_df = pd.DataFrame(detailed_log_data)
  log_df.to_excel(output_filename, index=False)

  if not log_df.empty:
        correct_count = log_df['Is_Correct'].sum()
        total_evaluated = len(log_df)
        accuracy = (correct_count / total_evaluated) * 100
        print(f"\n--- Final Geographic Accuracy for {dataset_path} ---")
        print(f"Accuracy: {accuracy:.2f}% ({correct_count} correct out of {total_evaluated} articles)")
  else:
        print("\nCould not evaluate geographic accuracy.")






In [ ]:
llama_pipeline = load_llama_pipeline()
run_analysis(llama_pipeline=llama_pipeline, dataset_path= test_df, output_filename='llama3_resolved_ner_historic_data.xlsx')


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


config.json:   0%|          | 0.00/654 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/23.9k [00:00<?, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

...

Device set to use cuda


Llama 3 model loaded successfully.
Loaded 614 articles for processing.


Processing                                                Article  \
0    Public Holiday Declared on February …

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more de


Detailed evaluation log saved to 'llama3_resolved_ner_historic_data.xlsx'

--- Final Geographic Accuracy for                                                Article  \
0    Public Holiday Declared on February 5 for Kash...   
1    Deadly Dumper Accidents Claim Five Lives in Ka...   
2    Fatal Collision on Quetta-Karachi Highway Near...   
3    BLF Claims Responsibility for Sniper Attack in...   
4    Gunmen Attack Construction Site in Khuzdar, Ba...   
..                                                 ...   
609  Protests in Mombasa. The Genz have started pro...   
610  Protests in Nairobi CBD. Poloce started hurlin...   
611  Drones Debris Recovered. Security forces in so...   
612  Crime. A taxi driver was killed, in a horrific...   
613  Protests in Kisii. Genz protests started in Ki...   

                    Primary Location  
0                           Pakistan  
1                  Karachi, Pakistan  
2          Quetta- Karachi, Pakistan  
3        Kech, Balochistan, Pakistan 

In [ ]:
from typing import Union, Tuple, Dict
import pandas as pd
from sklearn.metrics import classification_report, accuracy_score

ABSTAIN = "ABSTAIN"

def compute_location_metrics(log_source: Union[str, pd.DataFrame],save_per_class_csv: bool = True,per_class_outfile: str = "per_class_location_metrics.csv"):

    if isinstance(log_source, str):
        if log_source.lower().endswith((".xlsx", ".xls")):
            df = pd.read_excel(log_source)
        else:
            df = pd.read_csv(log_source)
    else:
        df = log_source.copy()




    def make_label(name: str, article: str):

        if not isinstance(name, str) or name.strip() == "" or name.strip().upper().startswith("NO_"):
            return ABSTAIN

        try:
            r = resolve_toponym(article, name)
        except Exception:
            r = None

        if r:
            try:
                disp = sanitize_location_string(r.raw.get("display_name", "") or name)
            except Exception:
                disp = sanitize_location_string(name)
        else:
            disp = sanitize_location_string(name)

        parts = [p.strip() for p in disp.split(",") if p.strip()]
        if len(parts) >= 3:
            return ", ".join(parts[:3])
        elif len(parts) == 2:
            return ", ".join(parts[:2])
        elif parts:
            return parts[0]
        return ABSTAIN

    y_true_labels = []
    y_pred_labels_eval = []

    for _, row in df.fillna("").iterrows():
        art  = str(row["Article"])
        y_t  = make_label(str(row["True_Location"]), art)
        y_p0 = make_label(str(row["Predicted_Location"]), art)

        is_correct = bool(row["Is_Correct"])
        y_p = y_t if is_correct else y_p0

        y_true_labels.append(y_t)
        y_pred_labels_eval.append(y_p)

    class_labels = sorted({c for c in y_true_labels if c != ABSTAIN})
    if not class_labels:
        raise ValueError("No non-ABSTAIN true labels found, cannot compute macro metrics.")

    report = classification_report(
        y_true_labels,
        y_pred_labels_eval,
        labels=class_labels,
        target_names=class_labels,
        output_dict=True,
        zero_division=0
    )

    overall_accuracy = report.get("accuracy", accuracy_score(y_true_labels, y_pred_labels_eval))
    macro_precision  = report["macro avg"]["precision"]
    macro_recall     = report["macro avg"]["recall"]
    macro_f1         = report["macro avg"]["f1-score"]

    per_class_df = pd.DataFrame(report).T.loc[class_labels, ["precision", "recall", "f1-score", "support"]]

    per_class_df.to_csv(per_class_outfile, index=True)

    if "Is_Correct" in df.columns and len(df):
        geo_acc = float(pd.to_numeric(df["Is_Correct"]).mean())
        print(f"Is_Correct mean: {geo_acc:.3f}")

    print("\n--- Location Classification Metrics  ---")
    print(f"Accuracy:        {overall_accuracy:.3f}")
    print(f"Macro Precision: {macro_precision:.3f}")
    print(f"Macro Recall:    {macro_recall:.3f}")
    print(f"Macro F1:        {macro_f1:.3f}")
    print("\nPer-class metrics (top 10 by support):")
    print(per_class_df.sort_values("support", ascending=False).head(10).round(3))

    return overall_accuracy, macro_precision, macro_recall, macro_f1, per_class_df

log_path = "llama3_resolved_ner_historic_data.xlsx"

overall_acc, mP, mR, mF1, per_class = compute_location_metrics(
    log_source=log_path,
    save_per_class_csv=True,
    per_class_outfile="per_class_location_metrics.csv"
)


Sanity check — Is_Correct mean: 0.893

--- Location Classification Metrics (rule-aligned) ---
Accuracy:        0.893
Macro Precision: 0.914
Macro Recall:    0.882
Macro F1:        0.893

Per-class metrics (top 10 by support):
                                  precision  recall  f1-score  support
Pakistan                              0.955   0.808     0.875     26.0
Karachi, Pakistan                     1.000   1.000     1.000     20.0
Baghdad, Iraq                         1.000   0.938     0.968     16.0
Democratic Republic of the Congo      0.917   0.786     0.846     14.0
Kharkiv oblast, Ukraine               1.000   1.000     1.000     12.0
Peshawar, Pakistan                    1.000   0.909     0.952     11.0
Quetta, Pakistan                      1.000   1.000     1.000     11.0
Kharkiv city, Ukraine                 1.000   0.900     0.947     10.0
Afghanistan                           0.909   1.000     0.952     10.0
Islamabad, Pakistan                   1.000   0.900     0.947   

# **ATROCITIES DATASET**

In [ ]:
atroc_test_df = pd.read_excel('walahi_final_atrocities_dataset.xlsx')
print(atroc_test_df.info())
atroc_test_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 646 entries, 0 to 645
Data columns (total 4 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Article           646 non-null    object 
 1   Primary Location  646 non-null    object 
 2   Latitude          646 non-null    float64
 3   Longitude         646 non-null    float64
dtypes: float64(2), object(2)
memory usage: 20.3+ KB
None


Article  \
0  Armed men shot dead the village chief of Chaha...   
1  Two female suicide bombers have killed at leas...   
2  At least 15 Agatu farmers were killed in Udeni...   
3  At least five persons were killed on Monday [4...   
4  No fewer than 16 persons have been reportedly ...   

                                    Primary Location   Latitude  Longitude  
0  Chahar Shanghoy village, Mangajek, Jowzjan, Af...  36.934167  66.113889  
1            Kouyape, Kolofata, Far North, Cameroon   11.020833  13.966389  
2      Udeni Ruwa District, Toto, Nasarawa, Nigeria    8.250000   7.198056  
3  Izge Gwoza and Izge Dambuwa villages, Gwoza LG...  11.176389  13.579167  
4  Ula Upata community,  Ahoada East LGA, Rivers,...   5.070278   6.642778

In [ ]:
atroc_test_df['Article']= atroc_test_df['Article'].apply(clean_text)

In [ ]:
atroc_test_df["Article"] = atroc_test_df["Article"].apply(get_first_n_sentences)

In [ ]:
def atroc_run_analysis(llama_pipeline, dataset_path, output_filename):



  detailed_log_data = []
  for _, row in tqdm(atroc_test_df.iterrows(), total=len(atroc_test_df), desc=f"Processing {atroc_test_df}"):
      article_text = row['Article']
      true_location_str = sanitize_location_string(row['Primary Location'])
      latitude = row['Latitude']
      longitude = row['Longitude']


      ner_candidates = extract_locations(article_text)

      if not ner_candidates:
        continue

      resolved_candidates = []
      for cand_str in ner_candidates:
          resolved = resolve_toponym(geolocator ,article_text, cand_str)
          if resolved:
              resolved_candidates.append(sanitize_location_string(resolved.address))
          else:
              resolved_candidates.append(sanitize_location_string(cand_str))

      if not resolved_candidates:
        continue

      pred_location_str = get_llama_prediction(llama_pipeline, article_text, list(set(resolved_candidates)))

      is_correct = False
      correctness_method = "Incorrect"
      resolved_true_str = ""
      resolved_pred_str = ""


      if "NO_" not in pred_location_str and true_location_str:

          pred_loc_obj = resolve_toponym(geolocator, article_text, pred_location_str)

          if pred_loc_obj:

              pred_loc_str = sanitize_location_string(pred_loc_obj.raw.get('display_name'))

              distance = geodesic((latitude, longitude), (pred_loc_obj.latitude, pred_loc_obj.longitude)).kilometers
              if distance <= 50:
                  is_correct = True
                  correctness_method = "Distance"


              else:
                  true_location_list = true_location_str.split(',')
                  pred_location_list = pred_loc_str.split(',')

                  if check_overlap(true_location_list[0], pred_location_list):
                    is_correct = True
                    correctness_method= "overlap resolved"

          else:
              true_location_list = true_location_str.split(',')
              pred_location_list = pred_location_str.split(',')
              if check_overlap(true_location_list[0], pred_location_list):
                  is_correct = True
                  correctness_method= "overlap not resolved"


      detailed_log_data.append({
            'Article': article_text,
            'NER_Candidates': ", ".join(ner_candidates),
            'Resolved_Candidates': ", ".join(resolved_candidates),
            'True_Location': true_location_str,
            'Predicted_Location': pred_location_str,
            'Is_Correct': is_correct,
            'Correctness_Method': correctness_method
        })


  log_df = pd.DataFrame(detailed_log_data)
  log_df.to_excel(output_filename, index=False)

  if not log_df.empty:
        correct_count = log_df['Is_Correct'].sum()
        total_evaluated = len(log_df)
        accuracy = (correct_count / total_evaluated) * 100
        print(f"\n--- Final Geographic Accuracy for {dataset_path} ---")
        print(f"Accuracy: {accuracy:.2f}% ({correct_count} correct out of {total_evaluated} articles)")
  else:
        print("\nCould not evaluate geographic accuracy.")






In [ ]:
atroc3_llama_pipeline = load_llama_pipeline()
atroc_run_analysis(llama_pipeline= atroc3_llama_pipeline, dataset_path= atroc_test_df, output_filename='llama3_resolved_ner_2atrocities_data.xlsx')


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda


Llama 3 model loaded successfully.
Loaded 646 articles for processing.


Processing                                                Article  \
0    Armed men shot dead the village chie…

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more de

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more de

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more de

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more de


Detailed evaluation log saved to 'llama3_resolved_ner_2atrocities_data.xlsx'

--- Final Geographic Accuracy for                                                Article  \
0    Armed men shot dead the village chief of Chaha...   
1    Two female suicide bombers have killed at leas...   
2    At least 15 Agatu farmers were killed in Udeni...   
3    At least five persons were killed on Monday [4...   
4    No fewer than 16 persons have been reportedly ...   
..                                                 ...   
641  Eight farmers were reportedly killed by gunmen...   
642  No fewer than 21 persons were confirmed dead f...   
643  A Nicaraguan opposition party CxL leader was k...   
644  Gunmen killed a TV and radio journalist in Afg...   
645  At least 20 people were killed and 16 hurt in ...   

                                      Primary Location   Latitude  Longitude  
0    Chahar Shanghoy village, Mangajek, Jowzjan, Af...  36.934167  66.113889  
1              Kouyape, Kolofata

In [ ]:
from typing import Union, Tuple, Dict
import pandas as pd
from sklearn.metrics import classification_report, accuracy_score

ABSTAIN = "ABSTAIN"

def compute_location_metrics(log_source: Union[str, pd.DataFrame],save_per_class_csv: bool = True,per_class_outfile: str = "per_class_location_metrics.csv"):

    if isinstance(log_source, str):
        if log_source.lower().endswith((".xlsx", ".xls")):
            df = pd.read_excel(log_source)
        else:
            df = pd.read_csv(log_source)
    else:
        df = log_source.copy()



    def make_label(name: str, article: str):

        if not isinstance(name, str) or name.strip() == "" or name.strip().upper().startswith("NO_"):
            return ABSTAIN

        try:
            r = resolve_toponym(article, name)
        except Exception:
            r = None

        if r:
            try:
                disp = sanitize_location_string(r.raw.get("display_name", "") or name)
            except Exception:
                disp = sanitize_location_string(name)
        else:
            disp = sanitize_location_string(name)

        parts = [p.strip() for p in disp.split(",") if p.strip()]
        if len(parts) >= 3:
            return ", ".join(parts[:3])
        elif len(parts) == 2:
            return ", ".join(parts[:2])
        elif parts:
            return parts[0]
        return ABSTAIN

    y_true_labels = []
    y_pred_labels_eval = []

    for _, row in df.fillna("").iterrows():
        art  = str(row["Article"])
        y_t  = make_label(str(row["True_Location"]), art)
        y_p0 = make_label(str(row["Predicted_Location"]), art)

        is_correct = bool(row["Is_Correct"])
        y_p = y_t if is_correct else y_p0

        y_true_labels.append(y_t)
        y_pred_labels_eval.append(y_p)

    class_labels = sorted({c for c in y_true_labels if c != ABSTAIN})
    if not class_labels:
        raise ValueError("No non-ABSTAIN true labels found, cannot compute macro metrics.")

    report = classification_report(
        y_true_labels,
        y_pred_labels_eval,
        labels=class_labels,
        target_names=class_labels,
        output_dict=True,
        zero_division=0
    )

    overall_accuracy = report.get("accuracy", accuracy_score(y_true_labels, y_pred_labels_eval))
    macro_precision  = report["macro avg"]["precision"]
    macro_recall     = report["macro avg"]["recall"]
    macro_f1         = report["macro avg"]["f1-score"]

    per_class_df = pd.DataFrame(report).T.loc[class_labels, ["precision", "recall", "f1-score", "support"]]
    if save_per_class_csv:
        per_class_df.to_csv(per_class_outfile, index=True)

    if "Is_Correct" in df.columns and len(df):
        geo_acc = float(pd.to_numeric(df["Is_Correct"]).mean())
        print(f"Is_Correct mean: {geo_acc:.3f}")

    print("\n--- Location Classification Metrics (rule-aligned) ---")
    print(f"Accuracy:        {overall_accuracy:.3f}")
    print(f"Macro Precision: {macro_precision:.3f}")
    print(f"Macro Recall:    {macro_recall:.3f}")
    print(f"Macro F1:        {macro_f1:.3f}")
    print("\nPer-class metrics (top 10 by support):")
    print(per_class_df.sort_values("support", ascending=False).head(10).round(3))

    return overall_accuracy, macro_precision, macro_recall, macro_f1, per_class_df

log_path = "llama3_resolved_ner_2atrocities_data.xlsx"

overall_acc, mP, mR, mF1, per_class = compute_location_metrics(
    log_source=log_path,
    save_per_class_csv=True,
    per_class_outfile="per_class_location_metrics.csv"
)


Sanity check — Is_Correct mean: 0.810

--- Location Classification Metrics (rule-aligned) ---
Accuracy:        0.810
Macro Precision: 0.808
Macro Recall:    0.801
Macro F1:        0.804

Per-class metrics (top 10 by support):
                                                    precision  recall  \
Peshawar, Peshawar District, North West Frontie...        1.0     1.0   
Beni, Beni, North Kivu                                    1.0     1.0   
Maiduguri, Maiduguri, Borno                               1.0     1.0   
Hodeida, Al Hawak, Al Hudaydah                            1.0     1.0   
Playa del Carmen, Solidaridad, Quintana Roo               1.0     1.0   
Acapulco, Acapulco de Juarez, Guerrero                    1.0     1.0   
Rio de Janeiro, Rio de Janeiro, Rio de Janeiro            1.0     1.0   
Zurmi, Zurmi, Zamfara                                     0.0     0.0   
Khartoum, Khartoum, Khartoum                              1.0     1.0   
Ghazni, Ghazni, Ghazni                      

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:98: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_true = type_of_target(y_true, input_name="y_true")
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:99: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_pred = type_of_target(y_pred, input_name="y_pred")
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  ys_types = set(type_of_target(x) for x in ys)
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater t

# **FEW SHOT**

In [ ]:
train_df = pd.read_excel('final_dataset.xlsx')
train_df.head()

Article    Category  \
0  Fatal daytime stabbing shocks Bamenda market d...       Crime   
1  Rio police seize 800kg of cocaine after shooto...       Crime   
2  Extortion‑linked arson wave guts San Pedro Sul...       Crime   
3  Chinese engineers abducted from Darfur road pr...  Kidnapping   
4  Tour bus hijacked outside Acapulco; 18 holiday...  Kidnapping   

                                      Location  
0          Bamenda, Northwest Region, Cameroon  
1          Nova Iguaçu, Rio de Janeiro, Brazil  
2  San Pedro Sula, Cortés Department, Honduras  
3                   Nyala, South Darfur, Sudan  
4                   Acapulco, Guerrero, Mexico

In [ ]:
def get_first_3_sentences(text: str, n: int = 3):

    sentences = re.split(r'(?<=[.!?])\s+', text)
    return " ".join(sentences[:n])

In [ ]:

train_df['Primary Location'] = train_df['Location']
train_df['Article'] = train_df['Article'].apply(clean_text)
train_df = train_df[['Article','Primary Location']].copy()
train_df["Article"] = train_df["Article"].apply(get_first_3_sentences)

In [ ]:
train_df.head()

Article  \
0  Fatal daytime stabbing shocks Bamenda market d...   
1  Rio police seize 800kg of cocaine after shooto...   
2  Extortion‑linked arson wave guts San Pedro Sul...   
3  Chinese engineers abducted from Darfur road pr...   
4  Tour bus hijacked outside Acapulco; 18 holiday...   

                              Primary Location  
0          Bamenda, Northwest Region, Cameroon  
1          Nova Iguaçu, Rio de Janeiro, Brazil  
2  San Pedro Sula, Cortés Department, Honduras  
3                   Nyala, South Darfur, Sudan  
4                   Acapulco, Guerrero, Mexico

In [ ]:
# def resolve_all_candidates(row):
#   resolved_list = []
#   for cand in row['NER_Candidates']:
#     article_text = row['Article']
#     resolved = resolve_toponym(geolocator ,article_text, cand)
#     if resolved:
#       resolved_list.append(sanitize_location_string(resolved.raw.get('display_name')))

#   return resolved_list

from typing import List
import random, textwrap

def prepare_examples(train_df):

  print("Extracting locations:")
  train_df['NER_Candidates'] = train_df['Article'].progress_apply(extract_locations)

  # print("Resolving candidates:")
  # train_df['Resolved_Candidates'] = train_df.progress_apply(resolve_all_candidates, axis=1)

  print("Creating examples:")

  train_df['embeddings'] = train_df['Article'].progress_apply(lambda x: embedding_model.encode(x, convert_to_tensor=True))

  return train_df


def get_dynamic_examples(target_article_text, examples_df,k = 3):

  target_embedding = embedding_model.encode(target_article_text, convert_to_tensor=True)


  pool_embeddings = torch.stack(examples_df['embeddings'].tolist())

  cos_similarities = util.cos_sim(target_embedding, pool_embeddings)

  top_k_indices = torch.topk(cos_similarities.flatten(), k=k).indices.tolist()

  top_k_rows = examples_df.iloc[top_k_indices]

  return top_k_rows


def create_llama_prompt(article_text, candidates, examples_df):

  # system_prompt = "You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the list."
  system_msg = {
        "role": "system",
        "content": (
            "You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the "
        )
    }

  shot_messages = []
  for _, ex in examples_df.iterrows():
      if not ex["NER_Candidates"]:
          continue

      cand_block = "\n- " + "\n- ".join(ex["NER_Candidates"])
      shot_user = {
          "role": "user",
          "content": textwrap.dedent(f"""
              Article:
              \"\"\"{ex['Article']}\"\"\"

              Location candidates:{cand_block}

              Which location from the candidates is primary location of the main event?
          """).strip()
      }
      shot_assistant = {
          "role": "assistant",
          "content": ex["Primary Location"].strip()
      }
      shot_messages.extend([shot_user, shot_assistant])

  cand_block = "\n- " + "\n- ".join(candidates)
  final_user = {
      "role": "user",
      "content": textwrap.dedent(f"""
          Article:
          \"\"\"{article_text}\"\"\"

          Location candidates:{cand_block}

          Which location from the candidates is primary location of the main event?
      """).strip()
  }

  return [system_msg] + shot_messages + [final_user]




def get_llama_prediction(llama_pipeline, prompt_messages: list):
    if not prompt_messages: return "NO_CANDIDATES_RESOLVED"

    prompt = llama_pipeline.tokenizer.apply_chat_template(
        prompt_messages,
        tokenize=False,
        add_generation_prompt=True
    )

    terminators = [
        llama_pipeline.tokenizer.eos_token_id,
        llama_pipeline.tokenizer.convert_tokens_to_ids("<|eot_id|>")
    ]

    try:
        sequences = llama_pipeline(prompt, num_return_sequences=1, eos_token_id=terminators, max_new_tokens=50, do_sample=False)
        prediction = sequences[0]['generated_text'][len(prompt):].strip()
        return prediction.split('\n')[0].strip()
    except Exception as e:
        print(f"An error occurred during Llama 3 inference: {e}")
        return "NO_PREDICTION_INFERENCE_ERROR"



In [ ]:
train_df = prepare_examples(train_df)

Extracting locations:


  0%|          | 0/1008 [00:00<?, ?it/s]

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


Creating examples:


  0%|          | 0/1008 [00:00<?, ?it/s]

In [ ]:
train_df.head()

Article  \
0  Fatal daytime stabbing shocks Bamenda market d...   
1  Rio police seize 800kg of cocaine after shooto...   
2  Extortion‑linked arson wave guts San Pedro Sul...   
3  Chinese engineers abducted from Darfur road pr...   
4  Tour bus hijacked outside Acapulco; 18 holiday...   

                              Primary Location  \
0          Bamenda, Northwest Region, Cameroon   
1          Nova Iguaçu, Rio de Janeiro, Brazil   
2  San Pedro Sula, Cortés Department, Honduras   
3                   Nyala, South Darfur, Sudan   
4                   Acapulco, Guerrero, Mexico   

                                      NER_Candidates  \
0  [Bafoussam, Yaoundé, Douala, Bamenda, Nkwen Ma...   
1  [Barra da Tijuca, São Paulo, Avenida Abílio Au...   
2     [San Pedro Sula, Tegucigalpa, Búfalo, Choloma]   
3  [Nyala, Khartoum, Port Sudan, Darfur, South Da...   
4  [Acapulco, Tuncingo, Las Cruces, Guerrero, Pue...   

                                          embeddings  
0  [tensor(0.0041, device='cuda:0'), tensor(0.039...  
1  [tensor(-0.0078, device='cuda:0'), tensor(0.09...  
2  [tensor(0.0386, device='cuda:0'), tensor(0.086...  
3  [tensor(-0.0160, device='cuda:0'), tensor(0.06...  
4  [tensor(0.0107, device='cuda:0'), tensor(0.082...

In [ ]:
shot_pipeline = load_llama_pipeline()
prompt = create_llama_prompt(train_df.iloc[0]['Article'], train_df.iloc[0]['NER_Candidates'], train_df[:3])

prompt= shot_pipeline.tokenizer.apply_chat_template(
        prompt,
        tokenize=False,
        add_generation_prompt=True
    )
print(prompt)


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda


Llama 3 model loaded successfully.
<|begin_of_text|><|start_header_id|>system<|end_header_id|>

You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
              """Fatal daytime stabbing shocks Bamenda market district. Vendors stocking pepper and plantains in Bamenda's busy Nkwen Market barely glanced up when a passenger bus from Douala hissed to a halt at the taxi rank: the regional capital in Cameroon's conflict‑scarred Northwest often sees traffic from Yaoundé and Bafoussam at this hour. But at 11:17 a.m."""

              Location candidates:
- Bafoussam
- Yaoundé
- Bamenda
- Cameroon
- Northwest
- Douala
- Nkwen Market

              Which location from the candidates is primary location of the main event?<|eot_id|><|start_header_id|>assistant<|end_he

In [ ]:
def few_shot_run_analysis(llama_pipeline, example_pool, dataset_path, output_filename: str):



    detailed_log_data = []
    for _, row in tqdm(atroc_test_df.iterrows(), total=len(atroc_test_df), desc=f"Processing {dataset_path}"):
        article_text = row['Article']
        true_location_str = sanitize_location_string(row['Primary Location'])
        latitude = row['Latitude']
        longitude = row['Longitude']

        ner_candidates = extract_locations(article_text)

        resolved_candidates = []
        for cand_str in ner_candidates:
            resolved = resolve_toponym(geolocator ,article_text, cand_str)
            if resolved:
                resolved_candidates.append(sanitize_location_string(resolved.address))
            else:
                resolved_candidates.append(sanitize_location_string(cand_str))


        if not resolved_candidates:
            continue

        dynamic_examples = get_dynamic_examples(article_text, example_pool, k=2)
        prompt_messages = create_llama_prompt(article_text, list(set(resolved_candidates)), dynamic_examples)
        print("prompt messages: ",prompt_messages)
        pred_location_str = get_llama_prediction(llama_pipeline, prompt_messages)

        is_correct, correctness_method, resolved_true_str, resolved_pred_str = False, "Incorrect", "", ""
        if "NO_" not in pred_location_str and true_location_str:

            pred_loc_obj = resolve_toponym(geolocator,article_text,pred_location_str)

            if pred_loc_obj:
                resolved_pred_str =  sanitize_location_string(pred_loc_obj.raw.get('display_name'))
                distance = geodesic((latitude, longitude), (pred_loc_obj.latitude, pred_loc_obj.longitude)).kilometers
                if distance <= 50:
                  is_correct = True
                  correctness_method = "Distance"


                else:
                    true_location_list = true_location_str.split(',')
                    pred_location_list = resolved_pred_str.split(',')

                    if check_overlap(true_location_list[0], pred_location_list):
                      is_correct = True
                      correctness_method= "overlap resolved"

                    else:
                      pred_location_list = pred_location_str.split(',')
                      if check_overlap(true_location_list[0], pred_location_list):
                        is_correct = True
                        correctness_method= "overlap resolved 2"

            else:
                true_location_list = true_location_str.split(',')
                pred_location_list = pred_location_str.split(',')
                if check_overlap(true_location_list[0], pred_location_list):
                    is_correct = True
                    correctness_method= "overlap not resolved"

        detailed_log_data.append({
            'Article': article_text,
            'NER_Candidates': ", ".join(ner_candidates),
            'Resolved_Candidates': ", ".join(resolved_candidates),
            'True_Location': true_location_str,
            'Predicted_Location': pred_location_str,
            'Is_Correct': is_correct,
            'Correctness_Method': correctness_method
        })


    log_df = pd.DataFrame(detailed_log_data)
    log_df.to_excel(output_filename, index=False)

    if not log_df.empty:
        correct_count = log_df['Is_Correct'].sum()
        total_evaluated = len(log_df)
        accuracy = (correct_count / total_evaluated) * 100
        print(f"\n--- Final Geographic Accuracy for {dataset_path} ---")
        print(f"Accuracy: {accuracy:.2f}% ({correct_count} correct out of {total_evaluated} articles)")
    else:
        print("\nCould not evaluate geographic accuracy.")


In [ ]:
shot_pipeline = load_llama_pipeline()
examples_df = prepare_examples(train_df)
few_shot_run_analysis(llama_pipeline=shot_pipeline, example_pool=examples_df, dataset_path= atroc_test_df, output_filename='shot_resolved_ner_atroc_data.xlsx')


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda


Llama 3 model loaded successfully.
Extracting locations:


  0%|          | 0/1008 [00:00<?, ?it/s]

...

prompt messages:  [{'role': 'system', 'content': 'You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the '}, {'role': 'user', 'content': 'Article:\n              """Mayoral candidate gunned down in Iguala as Guerrero\'s election violence intensifies In the latest escalation of Mexico\'s bloody campaign season, gunmen assassinated Julio César Vargas, the centre‑left PRD mayoral hopeful for Iguala, outside a taco stand on Juan N. Álvarez Avenue late Saturday. Two aides and a bystander were wounded when attackers fired at close range from a grey Nissan Versa before fleeing toward Taxco."""\n\n              Location candidates:\n- Iguala\n- Juan N. Álvarez Avenue\n- Guerrero\n- Mexico\n\n              Which location from the candidates is primary location of the main event?'}, {'role': 'assistant', 'content': 'Iguala, Guer

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


prompt messages:  [{'role': 'system', 'content': 'You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the '}, {'role': 'user', 'content': 'Article:\n              """Terror‑linked gunmen assassinate Kurdish judge who oversaw IS trials A prominent Kurdish judge known for prosecuting Islamic State members was shot dead outside a bakery in Sulaymaniyah on Tuesday morning, in what security officials called the city\'s first high‑profile assassination in nearly a decade. The victim, 58‑year‑old Farhad Salih, had led Iraq\'s special terrorism court in the autonomous region and survived two previous attempts on his life. Witnesses told police that two men on a black Yamaha motorcycle fired four rounds from a silenced pistol before speeding toward Kirkuk Road."""\n\n              Location candidates:\n- Kirkuk Road\n- Sulaymani

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


prompt messages:  [{'role': 'system', 'content': 'You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the '}, {'role': 'user', 'content': 'Article:\n              """Religious Festival Stampede in Sialkot Leaves Nine Dead, Dozens Injured Nine pilgrims, including four women and two teenagers, were crushed to death late Sunday after panic spread through a crowd of 15,000 at the annual Urs of Sufi saint Imam Ali Shah in Sialkot\'s congested Imam Sahib neighbourhood. Witnesses say a rumour of an electrical short‑circuit in the shrine\'s overhead fan caused devotees to rush toward a single exit gate, which had been partially blocked by street‑food stalls. Punjab Emergency Service Rescue 1122 reported 48 injuries; seven remain critical at Allama Iqbal Memorial Hospital."""\n\n              Location candidates:\n- Imam Sahib\n

In [ ]:
from typing import Union, Tuple, Dict
import pandas as pd
from sklearn.metrics import classification_report, accuracy_score

ABSTAIN = "ABSTAIN"

def compute_location_metrics(log_source: Union[str, pd.DataFrame],save_per_class_csv: bool = True,per_class_outfile: str = "per_class_location_metrics.csv") :



    if isinstance(log_source, str):
        if log_source.lower().endswith((".xlsx", ".xls")):
            df = pd.read_excel(log_source)
        else:
            df = pd.read_csv(log_source)
    else:
        df = log_source.copy()



    def make_label(name: str, article: str):

        if not isinstance(name, str) or name.strip() == "" or name.strip().upper().startswith("NO_"):
            return ABSTAIN

        try:
            r = resolve_toponym(article, name)
        except Exception:
            r = None

        if r:
            try:
                disp = sanitize_location_string(r.raw.get("display_name", "") or name)
            except Exception:
                disp = sanitize_location_string(name)
        else:
            disp = sanitize_location_string(name)

        parts = [p.strip() for p in disp.split(",") if p.strip()]
        if len(parts) >= 3:
            return ", ".join(parts[:3])
        elif len(parts) == 2:
            return ", ".join(parts[:2])
        elif parts:
            return parts[0]
        return ABSTAIN

    y_true_labels = []
    y_pred_labels_eval = []

    for _, row in df.fillna("").iterrows():
        art  = str(row["Article"])
        y_t  = make_label(str(row["True_Location"]), art)
        y_p0 = make_label(str(row["Predicted_Location"]), art)

        is_correct = bool(row["Is_Correct"])

        y_p = y_t if is_correct else y_p0

        y_true_labels.append(y_t)
        y_pred_labels_eval.append(y_p)

    class_labels = sorted({c for c in y_true_labels if c != ABSTAIN})
    if not class_labels:
        raise ValueError("No non-ABSTAIN true labels found, cannot compute macro metrics.")

    report = classification_report(
        y_true_labels,
        y_pred_labels_eval,
        labels=class_labels,
        target_names=class_labels,
        output_dict=True,
        zero_division=0
    )

    overall_accuracy = report.get("accuracy", accuracy_score(y_true_labels, y_pred_labels_eval))
    macro_precision  = report["macro avg"]["precision"]
    macro_recall     = report["macro avg"]["recall"]
    macro_f1         = report["macro avg"]["f1-score"]

    per_class_df = pd.DataFrame(report).T.loc[class_labels, ["precision", "recall", "f1-score", "support"]]
    if save_per_class_csv:
        per_class_df.to_csv(per_class_outfile, index=True)

    if "Is_Correct" in df.columns and len(df):
        geo_acc = float(pd.to_numeric(df["Is_Correct"]).mean())
        print(f"Is_Correct mean: {geo_acc:.3f}")

    print(f"Accuracy:        {overall_accuracy:.3f}")
    print(f"Macro Precision: {macro_precision:.3f}")
    print(f"Macro Recall:    {macro_recall:.3f}")
    print(f"Macro F1:        {macro_f1:.3f}")
    print("\nPer-class metrics (top 10 by support):")
    print(per_class_df.sort_values("support", ascending=False).head(10).round(3))

    return overall_accuracy, macro_precision, macro_recall, macro_f1, per_class_df

log_path = "shot_resolved_ner_atroc_data.xlsx"

overall_acc, mP, mR, mF1, per_class = compute_location_metrics(
    log_source=log_path,
    save_per_class_csv=True,
    per_class_outfile="per_class_location_metrics.csv"
)


Sanity check — Is_Correct mean: 0.876

--- Location Classification Metrics (rule-aligned) ---
Accuracy:        0.876
Macro Precision: 0.870
Macro Recall:    0.866
Macro F1:        0.867

Per-class metrics (top 10 by support):
                                                    precision  recall  \
Peshawar, Peshawar District, North West Frontie...        1.0   1.000   
Beni, Beni, North Kivu                                    1.0   1.000   
Maiduguri, Maiduguri, Borno                               1.0   1.000   
Hodeida, Al Hawak, Al Hudaydah                            1.0   1.000   
Playa del Carmen, Solidaridad, Quintana Roo               1.0   1.000   
Acapulco, Acapulco de Juarez, Guerrero                    1.0   1.000   
Rio de Janeiro, Rio de Janeiro, Rio de Janeiro            1.0   1.000   
Zurmi, Zurmi, Zamfara                                     1.0   0.667   
Khartoum, Khartoum, Khartoum                              1.0   1.000   
Ghazni, Ghazni, Ghazni                      

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:98: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_true = type_of_target(y_true, input_name="y_true")
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:99: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_pred = type_of_target(y_pred, input_name="y_pred")
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  ys_types = set(type_of_target(x) for x in ys)
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater t

In [ ]:
def historic_few_shot_run_analysis(llama_pipeline, example_pool, dataset_path, output_filename: str):


    detailed_log_data = []
    for _, row in tqdm(test_df.iterrows(), total=len(test_df), desc=f"Processing {dataset_path}"):
        article_text = row['Article']
        true_location_str = sanitize_location_string(row['Primary Location'])


        ner_candidates = extract_locations(article_text)

        resolved_candidates = []
        for cand_str in ner_candidates:
            resolved = resolve_toponym(geolocator ,article_text, cand_str)
            if resolved:
                resolved_candidates.append(sanitize_location_string(resolved.address))
            else:
                resolved_candidates.append(sanitize_location_string(cand_str))


        if not resolved_candidates:
            continue

        dynamic_examples = get_dynamic_examples(article_text, example_pool,k=1)
        prompt_messages = create_llama_prompt(article_text, list(set(resolved_candidates)), dynamic_examples)
        print("prompt messages: ",prompt_messages)
        pred_location_str = get_llama_prediction(llama_pipeline, prompt_messages)

        is_correct, correctness_method, resolved_true_str, resolved_pred_str = False, "Incorrect", "", ""
        if "NO_" not in pred_location_str and true_location_str:

            pred_loc_obj = resolve_toponym(geolocator,article_text,pred_location_str)
            true_loc_obj = resolve_toponym(geolocator,article_text,true_location_str)

            if pred_loc_obj and true_loc_obj:
                resolved_pred_str =  sanitize_location_string(pred_loc_obj.raw.get('display_name'))
                resolved_true_str = sanitize_location_string(true_loc_obj.raw.get('display_name'))
                distance = geodesic((true_loc_obj.latitude, true_loc_obj.longitude), (pred_loc_obj.latitude, pred_loc_obj.longitude)).kilometers
                if distance <= 50:
                  is_correct = True
                  correctness_method = "Distance"


                else:
                    true_location_list = resolved_true_str.split(',')
                    pred_location_list = resolved_pred_str.split(',')

                    if check_overlap(true_location_list[0], pred_location_list):
                      is_correct = True
                      correctness_method= "overlap resolved"

            else:
                true_location_list = true_location_str.split(',')
                pred_location_list = pred_location_str.split(',')
                if check_overlap(true_location_list[0], pred_location_list):
                    is_correct = True
                    correctness_method= "overlap not resolved"

        detailed_log_data.append({
            'Article': article_text,
            'NER_Candidates': ", ".join(ner_candidates),
            'Resolved_Candidates': ", ".join(resolved_candidates),
            'True_Location': true_location_str,
            'Predicted_Location': pred_location_str,
            'Is_Correct': is_correct,
            'Correctness_Method': correctness_method
        })


    log_df = pd.DataFrame(detailed_log_data)
    log_df.to_excel(output_filename, index=False)

    if not log_df.empty:
        correct_count = log_df['Is_Correct'].sum()
        total_evaluated = len(log_df)
        accuracy = (correct_count / total_evaluated) * 100
        print(f"Accuracy: {accuracy:.2f}% ({correct_count} correct out of {total_evaluated} articles)")
    else:
        print("\nCould not evaluate geographic accuracy.")


In [ ]:
historic_shot_pipeline = load_llama_pipeline()
examples_df = prepare_examples(train_df)
historic_few_shot_run_analysis(llama_pipeline=historic_shot_pipeline, example_pool=examples_df, dataset_path= test_df, output_filename='historic_shot_resolved_ner_atroc_data.xlsx')


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda


Llama 3 model loaded successfully.
Extracting locations:


  0%|          | 0/1008 [00:00<?, ?it/s]

...

prompt messages:  [{'role': 'system', 'content': 'You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the '}, {'role': 'user', 'content': 'Article:\n              """Explosive‑laden drone strikes oil depot in northern Iraqi city of Kirkuk Kirkuk — Iraqi officials say a presumed ISIS drone packed with grenades slammed into a fuel‑storage tank at the state‑run North Oil Company on Sunday night, igniting a blaze that burned for six hours and shut down the Kirkuk‑Ceyhan export pipeline. Civil‑defence brigades contained the fire before it reached adjacent tanks, but smoke plumes were visible 30 km away. Two guards suffered burns while trying to douse the flames with handheld extinguishers, health authorities said."""\n\n              Location candidates:\n- Ceyhan\n- Kirkuk\n- Kirkuk Kirkuk\n\n              Which location fr

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


prompt messages:  [{'role': 'system', 'content': 'You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the '}, {'role': 'user', 'content': 'Article:\n              """Taxi driver fatally stabbed during late-night robbery in Port Harcourt market district. Witnesses say 38-year‑old Chima Obi was attacked just after 01:30 outside the bustling Creek Road wholesale fish market, only a ten‑minute walk from the Rivers State Government House where security patrols are normally visible. Obi had collected two male passengers near the Oil Mill area of Aba early in the night and was returning to the Trans‑Amadi depot when he pulled over to buy bottled water."""\n\n              Location candidates:\n- Rivers State Government House\n- Aba\n- Trans ‑ Amadi\n- Oil Mill\n- Port Harcourt\n- Creek Road\n\n              Which location from

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


prompt messages:  [{'role': 'system', 'content': 'You are an expert geographic analyst. Your task is to choose the single primary location from a provided list of candidates, based on the context of a news article. Respond with only the name of the correct location from the '}, {'role': 'user', 'content': 'Article:\n              """Beirut electricity protests turn violent as demonstrators storm state utility HQ What began as a candlelit vigil on Martyrs\' Square comparing Lebanon\'s darkness to wartime Kyiv ended in running street battles Tuesday night after hundreds of protesters marched on Électricité du Liban (EDL) headquarters on Corniche El Nahr, hurling rocks and petrol bombs. Demonstrators accuse the cash‑strapped utility of imposing 20‑hour daily blackouts while executives squander loans meant for power‑plant maintenance. Riot police fired tear gas and deployed water cannons borrowed from the port authority after several youths breached the compound fence and set fire to a fle

In [ ]:
from typing import Union, Tuple, Dict
import pandas as pd
from sklearn.metrics import classification_report, accuracy_score

ABSTAIN = "ABSTAIN"

def compute_location_metrics(log_source: Union[str, pd.DataFrame],save_per_class_csv: bool = True,per_class_outfile: str = "per_class_location_metrics.csv") :

    if isinstance(log_source, str):
        if log_source.lower().endswith((".xlsx", ".xls")):
            df = pd.read_excel(log_source)
        else:
            df = pd.read_csv(log_source)
    else:
        df = log_source.copy()




    def make_label(name: str, article: str):

        if not isinstance(name, str) or name.strip() == "" or name.strip().upper().startswith("NO_"):
            return ABSTAIN

        try:
            r = resolve_toponym(article, name)
        except Exception:
            r = None

        if r:
            try:
                disp = sanitize_location_string(r.raw.get("display_name", "") or name)
            except Exception:
                disp = sanitize_location_string(name)
        else:
            disp = sanitize_location_string(name)

        parts = [p.strip() for p in disp.split(",") if p.strip()]
        if len(parts) >= 3:
            return ", ".join(parts[:3])
        elif len(parts) == 2:
            return ", ".join(parts[:2])
        elif parts:
            return parts[0]
        return ABSTAIN

    y_true_labels = []
    y_pred_labels_eval = []

    for _, row in df.fillna("").iterrows():
        art  = str(row["Article"])
        y_t  = make_label(str(row["True_Location"]), art)
        y_p0 = makelabel(str(row["Predicted_Location"]), art)

        is_correct = bool(row["Is_Correct"])
        y_p = y_t if is_correct else y_p0

        y_true_labels.append(y_t)
        y_pred_labels_eval.append(y_p)

    class_labels = sorted({c for c in y_true_labels if c != ABSTAIN})
    if not class_labels:
        raise ValueError("No non-ABSTAIN true labels found, cannot compute macro metrics.")

    report = classification_report(
        y_true_labels,
        y_pred_labels_eval,
        labels=class_labels,
        target_names=class_labels,
        output_dict=True,
        zero_division=0
    )

    overall_accuracy = report.get("accuracy", accuracy_score(y_true_labels, y_pred_labels_eval))
    macro_precision  = report["macro avg"]["precision"]
    macro_recall     = report["macro avg"]["recall"]
    macro_f1         = report["macro avg"]["f1-score"]

    per_class_df = pd.DataFrame(report).T.loc[class_labels, ["precision", "recall", "f1-score", "support"]]
    if save_per_class_csv:
        per_class_df.to_csv(per_class_outfile, index=True)

    if "Is_Correct" in df.columns and len(df):
        geo_acc = float(pd.to_numeric(df["Is_Correct"]).mean())
        print(f"Is_Correct mean: {geo_acc:.3f}")

    print("\n--- Location Classification Metrics ---")
    print(f"Accuracy:        {overall_accuracy:.3f}")
    print(f"Macro Precision: {macro_precision:.3f}")
    print(f"Macro Recall:    {macro_recall:.3f}")
    print(f"Macro F1:        {macro_f1:.3f}")
    print("\nPer-class metrics (top 10 by support):")
    print(per_class_df.sort_values("support", ascending=False).head(10).round(3))

    return overall_accuracy, macro_precision, macro_recall, macro_f1, per_class_df

log_path = "historic_shot_resolved_ner_atroc_data.xlsx"

overall_acc, mP, mR, mF1, per_class = compute_location_metrics(
    log_source=log_path,
    save_per_class_csv=True,
    per_class_outfile="per_class_location_metrics.csv"
)


Sanity check — Is_Correct mean: 0.926

--- Location Classification Metrics (rule-aligned) ---
Accuracy:        0.926
Macro Precision: 0.948
Macro Recall:    0.930
Macro F1:        0.936

Per-class metrics (top 10 by support):
                                  precision  recall  f1-score  support
Pakistan                              1.000   0.731     0.844     26.0
Karachi, Pakistan                     1.000   1.000     1.000     20.0
Baghdad, Iraq                         1.000   0.875     0.933     16.0
Democratic Republic of the Congo      0.923   0.857     0.889     14.0
Kharkiv oblast, Ukraine               1.000   1.000     1.000     12.0
Peshawar, Pakistan                    1.000   1.000     1.000     11.0
Quetta, Pakistan                      1.000   1.000     1.000     11.0
Kharkiv city, Ukraine                 1.000   0.900     0.947     10.0
Afghanistan                           0.909   1.000     0.952     10.0
Islamabad, Pakistan                   1.000   1.000     1.000   

In [ ]:
train_df.head()

Article    Category  \
0  Fatal daytime stabbing shocks Bamenda market d...       Crime   
1  Rio police seize 800kg of cocaine after shooto...       Crime   
2  Extortion‑linked arson wave guts San Pedro Sul...       Crime   
3  Chinese engineers abducted from Darfur road pr...  Kidnapping   
4  Tour bus hijacked outside Acapulco; 18 holiday...  Kidnapping   

                                      Location  \
0          Bamenda, Northwest Region, Cameroon   
1          Nova Iguaçu, Rio de Janeiro, Brazil   
2  San Pedro Sula, Cortés Department, Honduras   
3                   Nyala, South Darfur, Sudan   
4                   Acapulco, Guerrero, Mexico   

                                      NER_Candidates  \
0  [Northwest, Yaoundé, Bafoussam, Market, Camero...   
1  [Vitória, Nova Iguaçu, Rio, Barra da Tijuca, B...   
2  [Búfalo, Puerto Barrios, Tela, Honduran, San P...   
3  [Jebel Marra, Port Sudan, China, Al ‑ Fulah, N...   
4  [Cabo Delgado, Cuernavaca, Puebla, Chilpancing...   

                                          embeddings  
0  [tensor(-0.0467, device='cuda:0'), tensor(0.09...  
1  [tensor(-0.0127, device='cuda:0'), tensor(0.02...  
2  [tensor(0.0218, device='cuda:0'), tensor(0.074...  
3  [tensor(-0.0164, device='cuda:0'), tensor(0.08...  
4  [tensor(-0.0221, device='cuda:0'), tensor(0.08...

# **CHAIN OF THOUGHT**

In [ ]:
random_article_series = train_df.sample(n=1).iloc[0]

article_index = random_article_series.name
article_text = random_article_series['Article']
ner_candidates = random_article_series['NER_Candidates']
ground_truth_location = random_article_series['Primary Location']

print("article index: ",article_index)
print("article: ",article_text)
print("candidates: ",ner_candidates)
print("primary location: ",ground_truth_location)

article index:  706
article:  Stampede at Kinshasa stadium leaves 11 dead after CAF Champions League qualifier Kinshasa — Celebrations turned deadly in the Democratic Republic of Congo capital on Sunday when a gate failure triggered a crowd crush at the 80,000‑seat Stade des Martyrs following AS Vita Club's penalty‑shoot‑out victory over Sudan's Al‑Hilal Omdurman. Police said fans rushed toward a locked exit in Tribune A to greet players, causing a bottleneck. Stadium stewards tried to reopen the gate, but the metal bars jammed.
candidates:  ['Sudan', 'Democratic Republic of Congo', 'Kinshasa']
primary location:  Kinshasa, Democratic Republic of Congo


In [ ]:
#### STATIC EXAMPLES ARE USED FOR COT AS THERE IS NO WAY TO DO DYNAMIC WITH TRAINING DATASET BECAUSE OF NEEDED REASONING TEMPLATES



FEW_SHOT_EXAMPLES = [
    # {
    #     "article": (
    #         "Dutch backpacker killed in daylight machete robbery in Mombasa Old Town. "
    #         "Witnesses say 27-year-old Lotte Vermeer was walking from Fort Jesus towards "
    #         "the busy Marikiti market around 11:00 when two men armed with pangas snatched "
    #         "her canvas satchel and slashed her neck. Traders along Ndia Kuu Street told "
    #         "reporters the assailants sped away on a boda-boda taxi that later dumped the "
    #         "blood-stained weapon in Changamwe, some 12 km inland."
    #     ),
    #     "candidates": [
    #         "Fort Jesus", "Ndia Kuu Street", "Mombasa Old Town",
    #         "Marikiti", "Changamwe"
    #     ],
    #     "reasoning": (
    #         "1. **Identify the main event**: A robbery and murder of a Dutch backpacker\n"
    #         "2. **Analyze location context in the article**:\n"
    #         "   - \"killed in daylight machete robbery in Mombasa Old Town\" → Mombasa Old Town is stated as where the crime occurred\n"
    #         "   - \"walking from Fort Jesus towards the busy Marikiti market\" → landmarks only\n"
    #         "   - \"Traders along Ndia Kuu Street\" → witness location\n"
    #         "   - \"dumped the weapon in Changamwe\" → disposal site\n"
    #         "3. **Apply location hierarchy**: article explicitly says the crime happened in Mombasa Old Town\n"
    #         "4. **Verify context clues**: title & lead confirm\n"
    #         "5. **Conclusion**: Mombasa Old Town is the primary location"
    #     ),
    #     "answer": "Mombasa Old Town",
    # },
    {
        "article": (
            "Night express derails near Asyut, killing 18 and injuring dozens. A Cairo-bound "
            "overnight express carrying 412 passengers left the tracks on a sharp bend near "
            "Manfalut town at 02:17 Friday, sending four coaches tumbling into an irrigation "
            "canal and plunging sleeping riders into darkness and muddy water. Egypt's health "
            "ministry confirmed 18 fatalities and 73 injuries ..."
        ),
        "candidates": ["Manfalut", "Cairo", "Minya", "Egypt", "Asyut"],
        "reasoning": (
            "1. **Identify the main event**: Train derailment\n"
            "2. **Analyze location context**: \"near Manfalut town\" is most specific spot of the derailment\n"
            "3. **Apply hierarchy**: choose most specific\n"
            "4. **Verify context clues**: explicit phrase \"left the tracks near Manfalut\"\n"
            "5. **Conclusion**: Manfalut is primary location"
        ),
        "answer": "Manfalut",
    },
    {
        "article": (
            "Night-time armed robbery spree across Abidjan leaves seven dead and dozens injured. "
            "Residents of the Plateau business district say they first heard automatic gunfire "
            "across the Ébrié Lagoon shortly after 23:00. Within fifteen minutes masked assailants "
            "hit kiosks in Plateau, Treichville, Cocody and Yopougon ..."
        ),
        "candidates": [
            "Lagos", "Yopougon", "Paris", "Treichville", "Bassam",
            "Ébrié Lagoon", "Rue du Commerce", "Plateau", "Grand",
            "Abidjan", "Cocody", "Côte d'Ivoire"
        ],
        "reasoning": (
            "1. **Identify the main event**: Coordinated armed robbery spree\n"
            "2. **Analyze location context**: spree \"across Abidjan\" covers multiple districts\n"
            "3. **Apply hierarchy**: Abidjan encompasses all incidents\n"
            "4. **Verify context clues**: title states \"across Abidjan\"\n"
            "5. **Conclusion**: Abidjan is primary location"
        ),
        "answer": "Abidjan",
    },
]

COT_EXAMPLES_DF = pd.DataFrame(FEW_SHOT_EXAMPLES)

In [ ]:


def create_llama_prompt_cot(article_text: str, candidates: list, examples: pd.DataFrame):

    system_msg = {
        "role": "system",
        "content": textwrap.dedent("""\
            You are an expert geographic analyst.

            Respond in **two parts**:
              1. Chain-of-thought reasoning (following the 5 steps below).
              2. A separate line that starts with EXACTLY:  FINAL ANSWER:
                 followed by the single best location from the candidate list.

            Five-step reasoning template:
              1. Identify the main event
              2. Analyze location context
              3. Apply location hierarchy logic
              4. Verify with explicit context clues
              5. Conclusion (why this location)
            """)
    }

    shot_msgs = []
    for _, ex in COT_EXAMPLES_DF.iterrows():
        if not ex["candidates"]:
            continue

        cand_block = "\n- " + "\n- ".join(ex["candidates"])

        shot_user = {
            "role": "user",
            "content": textwrap.dedent(f"""\
                Article:
                \"\"\"{ex['article']}\"\"\"

                Location candidates:{cand_block}

                Which location from the candidates is primary location of the main event? Use the five-step reasoning format.
                """)
        }

        shot_assistant = {
            "role": "assistant",
            "content": textwrap.dedent(f"""\
                {ex['reasoning'].strip()}

                FINAL ANSWER: {ex['answer']}
                """)
        }

        shot_msgs.extend([shot_user, shot_assistant])

        cand_block = "\n- " + "\n- ".join(candidates)
        final_user = {
            "role": "user",
            "content": textwrap.dedent(f"""\
                Article:
                \"\"\"{article_text}\"\"\"

                Location candidates:{cand_block}

                Which location is primary?  Use the five-step reasoning format.
                """)
        }

    return [system_msg] + shot_msgs + [final_user]


#     example_prompts = []
#     for ex in examples:
#         cand_str = "\n- ".join(ex['candidates'])
#         formatted_reasoning = ex['reasoning'].replace('\\n', '\n')

#         user_example = f"""Article:
# "{ex['article']}"

# Location Candidates:
# - {cand_str}"""

#         assistant_example = f"""Reasoning:
# {formatted_reasoning}

# Primary Location:
# {ex['answer']}"""

#         example_prompts.append((user_example, assistant_example))

#     messages = [{"role": "system", "content": system_prompt}]

#     for user_ex, assistant_ex in example_prompts:
#         messages.append({"role": "user", "content": user_ex})
#         messages.append({"role": "assistant", "content": assistant_ex})

#     candidate_list_str = "\n- ".join(candidates)
#     current_prompt = f"""Article:
# "{article_text}"

# - {candidate_list_str}"""

#     messages.append({"role": "user", "content": current_prompt})

#     return messages








def get_llama_prediction_cot(llama_pipeline, prompt_messages) :

    if not prompt_messages:
        return "NO_CANDIDATES_RESOLVED"

    prompt = llama_pipeline.tokenizer.apply_chat_template(
        prompt_messages,
        tokenize=False,
        add_generation_prompt=True
    )

    print(prompt[-1000:])

    terminators = [
        llama_pipeline.tokenizer.eos_token_id,
        llama_pipeline.tokenizer.convert_tokens_to_ids("<|eot_id|>")
    ]


    sequences = llama_pipeline(
        prompt,
        num_return_sequences=1,
        eos_token_id=terminators,
        max_new_tokens=400,
        do_sample=True,
        temperature=0.3,
        top_p=0.9,
        pad_token_id=llama_pipeline.tokenizer.eos_token_id
    )

    prediction_text = sequences[0]['generated_text'][len(prompt):]


    if "FINAL ANSWER:" in prediction_text:
      answer = prediction_text.rsplit("FINAL ANSWER:", 1)[-1].strip().splitlines()[0]
      return answer

    return "PARSE_ERROR"

In [ ]:
import textwrap
from typing import List

def historic_cot_run_analysis(llama_pipeline, dataset_path, output_filename: str):



    detailed_log_data = []
    for _, row in tqdm(test_df.iterrows(), total=len(test_df), desc=f"Processing {dataset_path}"):
        article_text = row['Article']
        true_location_str = sanitize_location_string(row['Primary Location'])


        ner_candidates = extract_locations(article_text)

        resolved_candidates = []
        for cand_str in ner_candidates:
            resolved = resolve_toponym(geolocator ,article_text, cand_str)
            if resolved:
                resolved_candidates.append(sanitize_location_string(resolved.address))
            else:
                resolved_candidates.append(sanitize_location_string(cand_str))


        if not resolved_candidates:
            continue


        prompt_messages = create_llama_prompt_cot(article_text, list(set(resolved_candidates)), COT_EXAMPLES_DF)
        # print("\nprompt messages: ",prompt_messages)

        pred_location_str = get_llama_prediction_cot(llama_pipeline, prompt_messages)
        # print("\nprediction: ",pred_location_str)

        is_correct, correctness_method, resolved_true_str, resolved_pred_str = False, "Incorrect", "", ""
        if "NO_" not in pred_location_str and true_location_str:

            pred_loc_obj = resolve_toponym(geolocator,article_text,pred_location_str)
            true_loc_obj = resolve_toponym(geolocator,article_text,true_location_str)

            if pred_loc_obj and true_loc_obj:
                resolved_pred_str =  sanitize_location_string(pred_loc_obj.raw.get('display_name'))
                resolved_true_str = sanitize_location_string(true_loc_obj.raw.get('display_name'))
                distance = geodesic((true_loc_obj.latitude, true_loc_obj.longitude), (pred_loc_obj.latitude, pred_loc_obj.longitude)).kilometers
                if distance <= 50:
                  is_correct = True
                  correctness_method = "Distance"


                else:
                    true_location_list = resolved_true_str.split(',')
                    pred_location_list = resolved_pred_str.split(',')

                    if check_overlap(true_location_list[0], pred_location_list):
                      is_correct = True
                      correctness_method= "overlap resolved"

                    else:
                      true_location_list = true_location_str.split(',')
                      pred_location_list = pred_location_str.split(',')
                      if check_overlap(true_location_list[0], pred_location_list):
                          is_correct = True
                          correctness_method= "overlap 2 resolved"


            else:
                true_location_list = true_location_str.split(',')
                pred_location_list = pred_location_str.split(',')
                if check_overlap(true_location_list[0], pred_location_list):
                    is_correct = True
                    correctness_method= "overlap not resolved"

        detailed_log_data.append({
            'Article': article_text,
            'NER_Candidates': ", ".join(ner_candidates),
            'Resolved_Candidates': ", ".join(resolved_candidates),
            'True_Location': true_location_str,
            'Predicted_Location': pred_location_str,
            'Is_Correct': is_correct,
            'Correctness_Method': correctness_method
        })


    log_df = pd.DataFrame(detailed_log_data)
    log_df.to_excel(output_filename, index=False)

    if not log_df.empty:
        correct_count = log_df['Is_Correct'].sum()
        total_evaluated = len(log_df)
        accuracy = (correct_count / total_evaluated) * 100
        print(f"\n--- Final Geographic Accuracy for {dataset_path} ---")
        print(f"Accuracy: {accuracy:.2f}% ({correct_count} correct out of {total_evaluated} articles)")
    else:
        print("\nCould not evaluate geographic accuracy.")


In [ ]:
historic_cot_pipeline = load_llama_pipeline()

historic_cot_run_analysis(llama_pipeline=historic_cot_pipeline, dataset_path= test_df, output_filename='historic_cot_resolved_ner_atroc_data.xlsx')


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda


Llama 3 model loaded successfully.

--- Starting Analysis for                                                Article  \
0    Public Holiday Declared on February 5 for Kash...   
1    Deadly Dumper Accidents Claim Five Lives in Ka...   
2    Fatal Collision on Quetta-Karachi Highway Near...   
3    BLF Claims Responsibility for Sniper Attack in...   
4    Gunmen Attack Construction Site in Khuzdar, Ba...   
..                                                 ...   
609  Protests in Mombasa. The Genz have started pro...   
610  Protests in Nairobi CBD. Poloce started hurlin...   
611  Drones Debris Recovered. Security forces in so...   
612  Crime. A taxi driver was killed, in a horrific...   
613  Protests in Kisii. Genz protests started in Ki...   

                    Primary Location  
0                           Pakistan  
1                  Karachi, Pakistan  
2          Quetta- Karachi, Pakistan  
3        Kech, Balochistan, Pakistan  
4     Khuzdar, Balochistan, Pakistan  
..     

Processing                                                Article  \
0    Public Holiday Declared on February …

...


=== ACTUAL PROMPT BEING SENT ===
of drone, missile, and artillery attacks on Sumy Oblast between May 24 and 25, targeting both urban centers and border communities.Sumy City: A food production facility was struck by UAVs; material damage reported, no casualties confirmed.Konotop: Infrastructure object destroyed; adjacent streets suffered power outages. Firefighters contained localized fires.Border Areas: Shelling continued across at least 15 hromadas. 80+ strikes registered within 24 hours.Bilopillia and Seredyna-Buda: Artillery and drone strikes damaged homes and utility lines."""

                Location candidates:
- Konotop, , Konotop Raion, Sumy Oblast, -, Ukraine
- Seredyna, Yavoriv Urban Hromada, Yavoriv Raion, , Ukraine
- Buda, Hays County, Texas, United States
- Sumy Oblast, Ukraine
- Bilopillia, , Sumy Raion, Sumy Oblast, Ukraine
- Sumy, , Sumy Raion, Sumy Oblast, Ukraine

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
r<|end_header_id|>

Article:
                """Wana Quadcopter Attack I. A disturbing incident occurred in Wana tehsil, South Waziristan, where a quadcopter reportedly fired shells at a group of youth playing volleyball. The District Headquarters Hospital (DHQ) Wana confirmed that 22 individuals were injured, including several children, with two victims in critical condition.PTI MNA Zubair Khan Wazir condemned the attack, noting the panic and fear it triggered among locals, forcing many to remain indoors."""

                Location candidates:
- Lower South Waziristan District, Dera Ismail Khan Division, Khyber Pakhtunkhwa, , Pakistan
- Tehsil Headquarters Hospital, Grand Trunk Road, Rehman City Phase-, Ferozewala, Ferozewala Tehsil, Sheikhupura District, Lahore Division, Punjab, , Pakistan
- Wana, Monongalia County, West Virginia, , United States

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
djan"
5. **Conclusion**: Abidjan is primary location

                FINAL ANSWER: Abidjan<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
                """Mpox cases rise to 18 in Ethiopia. The number of mpox cases in Ethiopia has reached 18, including one death and two recoveries, with the first case detected in a 21-day-old infant in Moyale near the Kenyan border on May 25. The country has intensified health monitoring to curb the outbreak, while the Africa CDC warns of potential cross-border spread due to Moyale's proximity to Somalia and Kenya. Across Africa, mpox has caused 1,793 deaths out of 141,966 cases since last year, with 35,752 confirmed infections. Authorities remain on high alert to contain the virus."""

                Location candidates:
- Africa
- Moyale, Borena, Oromia Region, Ethiopia
- Ethiopia
- Somalia
- Kenya

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
mada, Kramatorsk Raion, Donetsk Oblast, -, Ukraine
- Oleksandrivka, Oleksandrivka settlement hromada, Kramatorsk Raion, Donetsk Oblast, -, Ukraine
- Zarichne, Lyman urban hromada, Kramatorsk Raion, Donetsk Oblast, -, Ukraine
- Novotroitske, Olhynka Settlement Hromada, Volnovakha Raion, Donetsk Oblast, -, Ukraine
- Ocheretyne, Ocheretyne settlement hromada, Pokrovskii Raion, Donetsk Oblast, , Ukraine
- Bilytske, Dobropillia urban hromada, Pokrovskii Raion, Donetsk Oblast, -, Ukraine
- Vladimirivka
- Sviatohirsk, Sviatohirsk urban hromada, Kramatorsk Raion, Donetsk Oblast, , Ukraine
- Shakhivska Hromada
- Siversk, Siversk urban hromada, Bakhmut Raion, Donetsk Oblast, -, Ukraine
- Bakhmut Raion, Donetsk Oblast, Ukraine
- Kostiantynivka, Kostiantynivka urban hromada, Kramatorsk Raion, Donetsk Oblast, -, Ukraine
- Kramatorsk Raion, Donetsk Oblast, Ukraine

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
 Abidjan encompasses all incidents
4. **Verify context clues**: title states "across Abidjan"
5. **Conclusion**: Abidjan is primary location

                FINAL ANSWER: Abidjan<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
                """AS Attack. AS conducted a dawn attack in Sonalia Security forces base in Burjeed area, approximately 7 km West of Baidoa. The Al-Shabaab militants launched the attack with a suicide car bombing. Numerous casualties are reported as the militants claim to have overrun the bases."""

                Location candidates:
- Baidoa, Baidoa District, Bay, South West, Somalia
- Burjeed
- Rua Sonalia, Vila Vnua, Lagoinha, Nova Iguau, Regio Geogrfica Imediata do Rio de Janeiro, Regio Metropolitana do Rio de Janeiro, Regio Geogrfica Intermediria do Rio de Janeiro, Rio de Janeiro, Southeast Region, -, Brazil

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade

In [ ]:
from typing import Union, Tuple, Dict
import pandas as pd
from sklearn.metrics import classification_report, accuracy_score

ABSTAIN = "ABSTAIN"

def compute_location_metrics( log_source: Union[str, pd.DataFrame], save_per_class_csv: bool = True,per_class_outfile: str = "per_class_location_metrics.csv"):

    if isinstance(log_source, str):
        if log_source.lower().endswith((".xlsx", ".xls")):
            df = pd.read_excel(log_source)
        else:
            df = pd.read_csv(log_source)
    else:
        df = log_source.copy()


    def make_label(name: str, article: str) :

        if not isinstance(name, str) or name.strip() == "" or name.strip().upper().startswith("NO_"):
            return ABSTAIN

        try:
            r = resolve_toponym(article, name)
        except Exception:
            r = None

        if r:
            try:
                disp = sanitize_location_string(r.raw.get("display_name", "") or name)
            except Exception:
                disp = sanitize_location_string(name)
        else:
            disp = sanitize_location_string(name)

        parts = [p.strip() for p in disp.split(",") if p.strip()]
        if len(parts) >= 3:
            return ", ".join(parts[:3])
        elif len(parts) == 2:
            return ", ".join(parts[:2])
        elif parts:
            return parts[0]
        return ABSTAIN

    y_true_labels = []
    y_pred_labels_eval = []

    for _, row in df.fillna("").iterrows():
        art  = str(row["Article"])
        y_t  = make_label(str(row["True_Location"]), art)
        y_p0 = make_label(str(row["Predicted_Location"]), art)

        is_correct = bool(row["Is_Correct"])
        y_p = y_t if is_correct else y_p0

        y_true_labels.append(y_t)
        y_pred_labels_eval.append(y_p)

    class_labels = sorted({c for c in y_true_labels if c != ABSTAIN})
    if not class_labels:
        raise ValueError("No non-ABSTAIN true labels found; cannot compute macro metrics.")

    report = classification_report(
        y_true_labels,
        y_pred_labels_eval,
        labels=class_labels,
        target_names=class_labels,
        output_dict=True,
        zero_division=0
    )

    overall_accuracy = report.get("accuracy", accuracy_score(y_true_labels, y_pred_labels_eval))
    macro_precision  = report["macro avg"]["precision"]
    macro_recall     = report["macro avg"]["recall"]
    macro_f1         = report["macro avg"]["f1-score"]

    per_class_df = pd.DataFrame(report).T.loc[class_labels, ["precision", "recall", "f1-score", "support"]]
    if save_per_class_csv:
        per_class_df.to_csv(per_class_outfile, index=True)

    if "Is_Correct" in df.columns and len(df):
        geo_acc = float(pd.to_numeric(df["Is_Correct"]).mean())
        print(f"Is_Correct mean: {geo_acc:.3f}")

    print("\n--- Location Classification Metrics ---")
    print(f"Accuracy:        {overall_accuracy:.3f}")
    print(f"Macro Precision: {macro_precision:.3f}")
    print(f"Macro Recall:    {macro_recall:.3f}")
    print(f"Macro F1:        {macro_f1:.3f}")
    print("\nPer-class metrics (top 10 by support):")
    print(per_class_df.sort_values("support", ascending=False).head(10).round(3))

    return overall_accuracy, macro_precision, macro_recall, macro_f1, per_class_df

log_path = "historic_cot_resolved_ner_atroc_data.xlsx"

overall_acc, mP, mR, mF1, per_class = compute_location_metrics(
    log_source=log_path,
    save_per_class_csv=True,
    per_class_outfile="per_class_location_metrics.csv"
)


Sanity check — Is_Correct mean: 0.864

--- Location Classification Metrics (rule-aligned) ---
Accuracy:        0.864
Macro Precision: 0.922
Macro Recall:    0.872
Macro F1:        0.890

Per-class metrics (top 10 by support):
                                  precision  recall  f1-score  support
Pakistan                              0.952   0.769     0.851     26.0
Karachi, Pakistan                     1.000   1.000     1.000     20.0
Baghdad, Iraq                         1.000   0.750     0.857     16.0
Democratic Republic of the Congo      0.688   0.786     0.733     14.0
Kharkiv oblast, Ukraine               1.000   1.000     1.000     12.0
Peshawar, Pakistan                    1.000   0.909     0.952     11.0
Quetta, Pakistan                      1.000   0.909     0.952     11.0
Kharkiv city, Ukraine                 1.000   0.800     0.889     10.0
Afghanistan                           0.900   0.900     0.900     10.0
Islamabad, Pakistan                   1.000   0.900     0.947   

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:99: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_pred = type_of_target(y_pred, input_name="y_pred")
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  ys_types = set(type_of_target(x) for x in ys)
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:99: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_pred = type_of_target(y_pred, input_name="y_pred")
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater t

In [ ]:
def atroc_cot_run_analysis(llama_pipeline, dataset_path, output_filename: str):



    detailed_log_data = []
    for _, row in tqdm(atroc_test_df.iterrows(), total=len(atroc_test_df), desc=f"Processing {dataset_path}"):
        article_text = row['Article']
        true_location_str = sanitize_location_string(row['Primary Location'])
        latitude = row['Latitude']
        longitude = row['Longitude']


        ner_candidates = extract_locations(article_text)

        resolved_candidates = []
        for cand_str in ner_candidates:
            resolved = resolve_toponym(geolocator ,article_text, cand_str)
            if resolved:
                resolved_candidates.append(sanitize_location_string(resolved.address))
            else:
                resolved_candidates.append(sanitize_location_string(cand_str))


        if not resolved_candidates:
            continue


        prompt_messages = create_llama_prompt_cot(article_text, list(set(resolved_candidates)), COT_EXAMPLES_DF)
        # print("\nprompt messages: ",prompt_messages)

        pred_location_str = get_llama_prediction_cot(llama_pipeline, prompt_messages)
        print("prediction: ",pred_location_str)
        print("\ntrue location: ",true_location_str)

        is_correct, correctness_method, resolved_true_str, resolved_pred_str = False, "Incorrect", "", ""
        if "NO_" not in pred_location_str and true_location_str:

            pred_loc_obj = resolve_toponym(geolocator,article_text,pred_location_str)

            if pred_loc_obj:
                resolved_pred_str =  sanitize_location_string(pred_loc_obj.raw.get('display_name'))
                distance = geodesic((latitude, longitude), (pred_loc_obj.latitude, pred_loc_obj.longitude)).kilometers
                if distance <= 50:
                  is_correct = True
                  correctness_method = "Distance"


                else:
                    true_location_list = true_location_str.split(',')
                    pred_location_list = resolved_pred_str.split(',')

                    if check_overlap(true_location_list[0], pred_location_list):
                      is_correct = True
                      correctness_method= "overlap resolved"

                    else:
                      pred_location_list = pred_location_str.split(',')
                      if check_overlap(true_location_list[0], pred_location_list):
                          is_correct = True
                          correctness_method= "overlap not resolved"

            else:
                true_location_list = true_location_str.split(',')
                pred_location_list = pred_location_str.split(',')
                if check_overlap(true_location_list[0], pred_location_list):
                    is_correct = True
                    correctness_method= "overlap not resolved"

        detailed_log_data.append({
            'Article': article_text,
            'NER_Candidates': ", ".join(ner_candidates),
            'Resolved_Candidates': ", ".join(resolved_candidates),
            'True_Location': true_location_str,
            'Predicted_Location': pred_location_str,
            'Is_Correct': is_correct,
            'Correctness_Method': correctness_method
        })


    log_df = pd.DataFrame(detailed_log_data)
    log_df.to_excel(output_filename, index=False)

    if not log_df.empty:
        correct_count = log_df['Is_Correct'].sum()
        total_evaluated = len(log_df)
        accuracy = (correct_count / total_evaluated) * 100
        print(f"\n--- Final Geographic Accuracy for {dataset_path} ---")
        print(f"Accuracy: {accuracy:.2f}% ({correct_count} correct out of {total_evaluated} articles)")
    else:
        print("\nCould not evaluate geographic accuracy.")


In [ ]:
atroc_cot_pipeline = load_llama_pipeline()

atroc_cot_run_analysis(llama_pipeline=atroc_cot_pipeline, dataset_path= atroc_test_df, output_filename='atroc_cot_resolved_ner_atroc_data.xlsx')


--> Step 4: Loading Llama 3 model (this may take a few minutes)...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda


Llama 3 model loaded successfully.

--- Starting Analysis for                                                Article  \
0    Armed men shot dead the village chief of Chaha...   
1    Two female suicide bombers have killed at leas...   
2    At least 15 Agatu farmers were killed in Udeni...   
3    At least five persons were killed on Monday [4...   
4    No fewer than 16 persons have been reportedly ...   
..                                                 ...   
641  Eight farmers were reportedly killed by gunmen...   
642  No fewer than 21 persons were confirmed dead f...   
643  A Nicaraguan opposition party CxL leader was k...   
644  Gunmen killed a TV and radio journalist in Afg...   
645  At least 20 people were killed and 16 hurt in ...   

                                      Primary Location   Latitude  Longitude  
0    Chahar Shanghoy village, Mangajek, Jowzjan, Af...  36.934167  66.113889  
1              Kouyape, Kolofata, Far North, Cameroon   11.020833  13.966389  
2   

Processing                                                Article  \
0    Armed men shot dead the village chie…

...


=== ACTUAL PROMPT BEING SENT ===
d|>

1. **Identify the main event**: Coordinated armed robbery spree
2. **Analyze location context**: spree "across Abidjan" covers multiple districts
3. **Apply hierarchy**: Abidjan encompasses all incidents
4. **Verify context clues**: title states "across Abidjan"
5. **Conclusion**: Abidjan is primary location

                FINAL ANSWER: Abidjan<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
                """A clash between herders and farmers in Gora Village of Katsina State has left many people dead, the News Agency of Nigeria reports. No fewer than 12 persons were feared dead and nine injured during the clash at Gora Village of Safana Local Government Area of Katsina State. """

                Location candidates:
- Katsina State, Nigeria
- Safana Local Government Area
- Gora, Town of Petrinja, Sisak-Moslavina County, Croatia

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
Verify context clues**: title states "across Abidjan"
5. **Conclusion**: Abidjan is primary location

                FINAL ANSWER: Abidjan<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
                """29 people (including one policemen) were reportedly killed by suspected Fulani herdsmen following a fresh attack on Karmai Village in Maro Ward, Kajuru Local Government Area of Kaduna State. The attack was believed to be yet another reprisal over the recent killing of Fulani people in the area. The gunmen said to be in hundreds, were said to have invaded the community early yesterday (Tuesday) morning, shooting at people and burning houses.  """

                Location candidates:
- Kajuru Local Government Area
- Kaduna State, Nigeria
- Karmai Village
- Maro Way, Delft, Cape Town Ward , City of Cape Town, Western Cape, , South Africa

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
trict, Western Province, Sri Lanka
- The Shangri-La, , Downtown Las Vegas, Las Vegas, Clark County, Nevada, , United States
- Negombo, Gampaha District, Western Province, , Sri Lanka
- Jok one Table Dumplings, Soi Charoen Krung , Pom Prap Subdistrict, Pom Prap Sattru Phai District, Bangkok, , Thailand
- Kingsbury, LaPorte County, Indiana, United States
- Mount Lavinia, Station Road, Ratmalana, Dehiwala, Colombo District, Western Province, , Sri Lanka
- Sri Lanka
- St. Antony S, Pillaiyar Kovil Road, Mutur, Trincomalee District, Eastern Province, Sri Lanka
- Cinnamon Grand Colombo, , Galle Road, Liberty Circle, Kollupitiya, Slave Island, Colombo, Colombo District, Western Province, , Sri Lanka
- Dehiwala, Colombo District, Western Province, , Sri Lanka
- Shangri-La, Diqing, Yunnan, China
- Zion Church, Xuhang, Jiading District, China
- St. Sebastian s

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
au
- Grand
- Abidjan
- Cocody
- Côte d'Ivoire

                Which location from the candidates is primary location of the main event? Use the five-step reasoning format.<|eot_id|><|start_header_id|>assistant<|end_header_id|>

1. **Identify the main event**: Coordinated armed robbery spree
2. **Analyze location context**: spree "across Abidjan" covers multiple districts
3. **Apply hierarchy**: Abidjan encompasses all incidents
4. **Verify context clues**: title states "across Abidjan"
5. **Conclusion**: Abidjan is primary location

                FINAL ANSWER: Abidjan<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
                """A television journalist was shot to death shortly after leaving his station in the north coast city of Puerto Cortes Monday night."""

                Location candidates:
- Puerto Corts, Corts, , Honduras

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade


=== ACTUAL PROMPT BEING SENT ===
ch location from the candidates is primary location of the main event? Use the five-step reasoning format.<|eot_id|><|start_header_id|>assistant<|end_header_id|>

1. **Identify the main event**: Coordinated armed robbery spree
2. **Analyze location context**: spree "across Abidjan" covers multiple districts
3. **Apply hierarchy**: Abidjan encompasses all incidents
4. **Verify context clues**: title states "across Abidjan"
5. **Conclusion**: Abidjan is primary location

                FINAL ANSWER: Abidjan<|eot_id|><|start_header_id|>user<|end_header_id|>

Article:
                """Gunmen, suspected to be Fulani herdsmen, attacked Kwatas village in Bokkos Local Government Area of the Plateau state, killing 15 people. Several more were injured. """

                Location candidates:
- Plateau State, Nigeria
- Bokkos Local Government Area
- Kwatas

                Which location is primary?  Use the five-step reasoning format.<|eot_id|><|start_heade

In [ ]:
from typing import Union, Tuple, Dict
import pandas as pd
from sklearn.metrics import classification_report, accuracy_score

ABSTAIN = "ABSTAIN"

def compute_location_metrics(log_source: Union[str, pd.DataFrame],save_per_class_csv: bool = True,per_class_outfile: str = "per_class_location_metrics.csv"):
    if isinstance(log_source, str):
        if log_source.lower().endswith((".xlsx", ".xls")):
            df = pd.read_excel(log_source)
        else:
            df = pd.read_csv(log_source)
    else:
        df = log_source.copy()


    def make_label(name: str, article: str):

        if not isinstance(name, str) or name.strip() == "" or name.strip().upper().startswith("NO_"):
            return ABSTAIN

        try:
            r = resolve_toponym(article, name)
        except Exception:
            r = None

        if r:
            try:
                disp = sanitize_location_string(r.raw.get("display_name", "") or name)
            except Exception:
                disp = sanitize_location_string(name)
        else:
            disp = sanitize_location_string(name)

        parts = [p.strip() for p in disp.split(",") if p.strip()]
        if len(parts) >= 3:
            return ", ".join(parts[:3])
        elif len(parts) == 2:
            return ", ".join(parts[:2])
        elif parts:
            return parts[0]
        return ABSTAIN

    y_true_labels = []
    y_pred_labels_eval = []

    for _, row in df.fillna("").iterrows():
        art  = str(row["Article"])
        y_t  = make_label(str(row["True_Location"]), art)
        y_p0 = make_label(str(row["Predicted_Location"]), art)

        is_correct = bool(row["Is_Correct"])
        y_p = y_t if is_correct else y_p0

        y_true_labels.append(y_t)
        y_pred_labels_eval.append(y_p)

    class_labels = sorted({c for c in y_true_labels if c != ABSTAIN})
    if not class_labels:
        raise ValueError("No non-ABSTAIN true labels found, cannot compute macro metrics.")

    report = classification_report(
        y_true_labels,
        y_pred_labels_eval,
        labels=class_labels,
        target_names=class_labels,
        output_dict=True,
        zero_division=0
    )

    overall_accuracy = report.get("accuracy", accuracy_score(y_true_labels, y_pred_labels_eval))
    macro_precision  = report["macro avg"]["precision"]
    macro_recall     = report["macro avg"]["recall"]
    macro_f1         = report["macro avg"]["f1-score"]

    per_class_df = pd.DataFrame(report).T.loc[class_labels, ["precision", "recall", "f1-score", "support"]]
    if save_per_class_csv:
        per_class_df.to_csv(per_class_outfile, index=True)

    if "Is_Correct" in df.columns and len(df):
        geo_acc = float(pd.to_numeric(df["Is_Correct"]).mean())
        print(f"Is_Correct mean: {geo_acc:.3f}")

    print("\n--- Location Classification Metrics ---")
    print(f"Accuracy:        {overall_accuracy:.3f}")
    print(f"Macro Precision: {macro_precision:.3f}")
    print(f"Macro Recall:    {macro_recall:.3f}")
    print(f"Macro F1:        {macro_f1:.3f}")
    print("\nPer-class metrics (top 10 by support):")
    print(per_class_df.sort_values("support", ascending=False).head(10).round(3))

    return overall_accuracy, macro_precision, macro_recall, macro_f1, per_class_df

log_path = "atroc_cot_resolved_ner_atroc_data.xlsx"

overall_acc, mP, mR, mF1, per_class = compute_rule_aligned_location_metrics(
    log_source=log_path,
    save_per_class_csv=True,
    per_class_outfile="per_class_location_metrics.csv"
)


Sanity check — Is_Correct mean: 0.866

--- Location Classification Metrics (rule-aligned) ---
Accuracy:        0.866
Macro Precision: 0.859
Macro Recall:    0.855
Macro F1:        0.856

Per-class metrics (top 10 by support):
                                                    precision  recall  \
Peshawar, Peshawar District, North West Frontie...        1.0   1.000   
Beni, Beni, North Kivu                                    1.0   0.833   
Maiduguri, Maiduguri, Borno                               1.0   1.000   
Hodeida, Al Hawak, Al Hudaydah                            1.0   1.000   
Playa del Carmen, Solidaridad, Quintana Roo               1.0   1.000   
Acapulco, Acapulco de Juarez, Guerrero                    1.0   1.000   
Rio de Janeiro, Rio de Janeiro, Rio de Janeiro            1.0   1.000   
Zurmi, Zurmi, Zamfara                                     1.0   0.667   
Khartoum, Khartoum, Khartoum                              1.0   1.000   
Ghazni, Ghazni, Ghazni                      

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:98: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_true = type_of_target(y_true, input_name="y_true")
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:99: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  type_pred = type_of_target(y_pred, input_name="y_pred")
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater than 50% of the number of samples. `y` could represent a regression problem, not a classification problem.
  ys_types = set(type_of_target(x) for x in ys)
/usr/local/lib/python3.11/dist-packages/sklearn/utils/multiclass.py:79: UserWarning: The number of unique classes is greater t